![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Komputerowe wspomaganie tłumaczenia </h1>
<h2> 15. <i>Korekta gramatyczna</i> [laboratoria]</h2> 
<h3>Rafał Jaworski (2021)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

Ostatnią z omawianych przez nas technik stosowaną podczas wspomagania tłumaczenia jest korekta gramatyczna. Automatyczna korekta gramatyczna tekstu to ambitne zadanie odnalezienia możliwych błędów niezwiązanych bezpośrednio z pisownią. Są to między innymi:
* błędy gramatyczne
* źle użyte słowa
* złe połączenia wyrazowe
* błędy interpunkcyjne
* kolokwializmy
* redundancja (np. "tylko i wyłącznie")

Warto zwrócić uwagę, iż systemy do korekcji gramatycznej można traktować jako klasyfikatory binarne. Przyjmijmy, że odpowiedź pozytywna korektora to wykrycie błędu w tekście, natomiast negatywna - brak błędu. Wówczas rozróżniamy dwa typy pomyłek: false positive oraz false negative. False positive to tzw. "fałszywy alarm" - zbyt duża ich ilość spowoduje wydłużenie czasu pracy użytkownika przez konieczność analizowania zgłoszeń, które w istocie błędami nie są. Co jednak jeszcze gorsze, zbyt duża ilość false positives powoduje spadek zaufania użytkownika do systemu oraz drastyczny spadek satysfakcji z używania systemu. Te drugie błędy - false negatives - to z kolei faktyczne błędy w tekście, które nie zostały wyłapane przez system korekty. Stare polskie porzekadło głosi, że "czego oko nie widzi, tego sercu nie żal". Niestety jednak problem pojawia się, kiedy dostrzeże to jakieś inne oko... Wysoka liczba false negatives wprawdzie skraca czas korekty (sic!), ale odbywa się to kosztem jakości całego procesu. Idealnie zatem byłoby zminimalizować zarówno liczbę false positives, jak i false negatives. Jak jednak łatwo się domyślić, nie jest to zawsze możliwe. Korektor gramatyczny, który jest bardzo restrykcyjny i raportuje wiele błędów, będzie miał tendencję do popełniania false positives. Natomiast korektor bardziej pobłażliwy niechybnie popełni wiele false negatives. Co zatem jest ważniejsze? Praktyka wskazuje, że oba parametry mają podobną wagę, ale jednak odrobinę ważniejsze jest powstrzymanie się od false positives.

Do najbardziej popularnych narzędzi wspomagających korektę gramatyczną tekstu należą Grammarly oraz LanguageTool. Na dzisiejszych zajęciach zajmiemy się tym drugim. LanguageTool został pierwotnie napisany jako praca dyplomowa Daniela Nabera, a następnie intensywnie rozwijany wspólnie z Marcinem Miłkowskim. Aż do dziś projekt jest ciągle rozwijany, zwiększana jest liczba obsługiwanych języków oraz dokładność działania.

LanguageTool jest systemem opartym na regułach. W dobie wszechobecnej sztucznej inteligencji opartej na uczeniu maszynowym rozwiązanie to wydaje się nieco przestarzałe. Jednak to właśnie reguły stanowią o sile LanguageToola - pozwalają one na zwiększenie precyzji korektora poprzez minimalizację false positives. Warto wspomnieć, iż liczne reguły LanguageToola dotyczą również korekty pisowni. Czyni to z LanguageToola kompletne narzędzie do korekty tekstu. Polecam przejrzenie zestawu reguł LanguageToola dla języka angielskiego: https://community.languagetool.org/rule/list?lang=en

Czas uruchomić to narzędzie. Skorzystajmy z Pythona.

Następnie możemy użyć LanguageToola w programie Pythonowym: (przykład zaczerpnięty z oficjalnego tutoriala: https://pypi.org/project/language-tool-python/)

In [2]:
import language_tool_python
import pprint
tool = language_tool_python.LanguageTool('en-US') 

text = 'A sentence with a error in the Hitchhiker’s Guide tot he Galaxy'

pp = pprint.PrettyPrinter(depth=2)
errors = tool.check(text)
pp.pprint(errors)

Unzipping C:\Users\osins\AppData\Local\Temp\tmptnrydd9g.zip to C:\Users\osins\.cache\language_tool_python.
Downloaded https://www.languagetool.org/download/LanguageTool-6.4.zip to C:\Users\osins\.cache\language_tool_python.


[Match({'ruleId': 'EN_A_VS_AN', 'message': 'Use “an” instead of ‘a’ if the following word starts with a vowel sound, e.g. ‘an article’, ‘an hour’.', 'replacements': ['an'], 'offsetInContext': 16, 'context': 'A sentence with a error in the Hitchhiker’s Guide tot he ...', 'offset': 16, 'errorLength': 1, 'category': 'MISC', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"}),
 Match({'ruleId': 'TOT_HE', 'message': 'Did you mean “to the”?', 'replacements': ['to the'], 'offsetInContext': 43, 'context': '... with a error in the Hitchhiker’s Guide tot he Galaxy', 'offset': 50, 'errorLength': 6, 'category': 'TYPOS', 'ruleIssueType': 'misspelling', 'sentence': "A sentence with a error in the Hitchhiker's Guide tot he Galaxy"})]


Przeanalizujmy format zwracanego wyniku. Otrzymujemy listę obiektów Match - zawiadomień o potencjalnym błędzie. Razem z każdym błędem otrzymujemy m.in. identyfikator użytej reguły, opis błędu, rekomendancję poprawy, kontekst.

### Ćwiczenie 1: Użyj LanguageTool do znalezienia jak największej liczby prawdziwych błędów na swoim ulubionym portalu internetowym. Skorzystaj z poznanych wcześniej technik web scrapingu. Uwaga - LanguageTool najprawdopodobniej oznaczy nazwy własne jako literówki - ten typ błędu nie powinien być brany pod uwagę.

In [18]:
import re
import requests
from bs4 import BeautifulSoup
import language_tool_python
import pprint


def get_text(url):

    page = requests.get(url)
    soup = BeautifulSoup(page.content, 'html.parser')

    # usunięcie elementów script i style
    for script in soup(["script", "style"]):
        script.extract()    # usuń element

    # pobierz tekst
    text = soup.get_text()

    # usuń wielokrotne białe znaki
    text = re.sub(r"\s+", " ", text)

    return(text)


def find_errors(website_url):
    err = []
    text = get_text(website_url)
    tool = language_tool_python.LanguageTool('pl')
    errors = tool.check(text)
    for error in errors:
        if error.ruleId != 'MORFOLOGIK_RULE_PL_PL':
            err.append(error)    
       
    pp.pprint(err)
    return err

find_errors('https://skyblue.education/blog/2022/05/23/jak-wygladaja-aktywnosci-i-warsztaty-podczas-polkolonii-sky-blue/') #firma w której pracowałem

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "półkolonieróżne"?', 'replacements': ['półkolonieróżne'], 'offsetInContext': 43, 'context': '...dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty po...', 'offset': 316, 'errorLength': 15, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': '- Sky Blue Education Blog Półkolonie Kontakt O nas Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty podczas półkolonii Sky Blue?'}),
 Match({'ruleId': 'UPPERCASE_SENTENCE_START', 'message': 'To zdanie nie zaczyna się wielką literą', 'replacements': ['Zobacz'], 'offsetInContext': 43, 'context': '... warsztaty podczas półkolonii Sky Blue? zobacz także: Jak sk

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "półkolonieróżne"?', 'replacements': ['półkolonieróżne'], 'offsetInContext': 43, 'context': '...dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty po...', 'offset': 316, 'errorLength': 15, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': '- Sky Blue Education Blog Półkolonie Kontakt O nas Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Programowanie Minecraft Python Tworzenie stron Języki obce Dla dzieci Dla dorosłych Półkolonie Blog O nas Kontakt PółkolonieRóżne Jak wyglądają aktywności i warsztaty podczas półkolonii Sky Blue?'}),
 Match({'ruleId': 'UPPERCASE_SENTENCE_START', 'message': 'To zdanie nie zaczyna się wielką literą', 'replacements': ['Zobacz'], 'offsetInContext': 43, 'context': '... warsztaty podczas półkolonii Sky Blue? zobacz także: Jak sk

In [19]:
find_errors('https://wmi.amu.edu.pl/dla-kandydata/studia-i-stopnia/nauczanie-matematyki-i-informatyki')

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "treśćprzejdź"?', 'replacements': ['treśćprzejdź'], 'offsetInContext': 43, 'context': '...rzeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPr...', 'offset': 264, 'errorLength': 12, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': 'Nauczanie matematyki i informatyki | Wydział Matematyki i Informatyki Brak obsługi JavaScript Do pełnej funkcjonalności strony potrzebujesz włączonej obsługi skryptów. Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPrzejdź do Dostępność A A A en pl Wyszukaj Wyszukaj Nawigacja mobilna Wydział - Wydział Matematyki i Informatyki Wydział - Wydział Matematyki i Informatyki NO XML TR1A Wydział Pokaż menu szczegółowe Powrót do głównego menu O wydziale Władze wydziału Struktu

[Match({'ruleId': 'NIETYPOWA_KOMBINACJA_DUZYCH_I_MALYCH_LITER', 'message': 'Nietypowa kombinacja małych i dużych liter. Czy nie powinno być: "treśćprzejdź"?', 'replacements': ['treśćprzejdź'], 'offsetInContext': 43, 'context': '...rzeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPr...', 'offset': 264, 'errorLength': 12, 'category': 'CASING', 'ruleIssueType': 'misspelling', 'sentence': 'Nauczanie matematyki i informatyki | Wydział Matematyki i Informatyki Brak obsługi JavaScript Do pełnej funkcjonalności strony potrzebujesz włączonej obsługi skryptów. Instrukcje, które pozwolą Ci włączyć skrypty w Twojej przeglądarce znajdziesz tutaj Przejdź do TreśćPrzejdź do Menu głównePrzejdź do Mapa serwisuPrzejdź do Dostępność A A A en pl Wyszukaj Wyszukaj Nawigacja mobilna Wydział - Wydział Matematyki i Informatyki Wydział - Wydział Matematyki i Informatyki NO XML TR1A Wydział Pokaż menu szczegółowe Powrót do głównego menu O wydziale Władze wydziału Struktu

### Ćwiczenie 2: Napisz skrypt, który poszuka błędów w komentarzach klasy Javowej (zwykłych // oraz w javadocach). Uruchom ten skrypt na źródłach wybranego opensourcowego projektu w Javie.

In [44]:
def x(text):
    
    text = re.sub(r'<[^>]+>', '', text)
    text = re.sub(r'@[a-z]+', '', text)
    text = re.sub(r'\*', '', text)
    text = re.sub(r'\\', '', text)
    text = re.sub(r' \s+', ' ', text)
    return text.strip()

delete_tags_and_params('* \\kom <p>tag <b>tekst</b> @parametr <a href="#">link</a>.</p>')

'kom tag tekst link.'

In [48]:
import re
import language_tool_python
    
def correct_java_grammar(java_file_path):
    tool = language_tool_python.LanguageTool('en-US')
    lineToAnalyze = ""
    with open(java_file_path, 'r') as file:
        javadoc_mode = False
        for line in file:
            line.strip()
            #print(line)
            if line.startswith('//'):
                lineToAnalyze += line + " "
            elif line.startswith('/*') and line.endswith('*/'):
                lineToAnalyze += line + " "
            elif line.startswith('/*') and not line.endswith('*/'):
                lineToAnalyze += line + " "
                javadoc_mode = True
            
            elif javadoc_mode:
                if line.endswith('*/'):
                    javadoc_mode = False
                    lineToAnalyze += line + " "
                else:
                    lineToAnalyze += line + " "

        #print(x(lineToAnalyze))
        errors = tool.check(x(lineToAnalyze))
        

    return [errors for errors in errors if errors.ruleId != 'MORFOLOGIK_RULE_EN_US']

correct_java_grammar("./class.java") # kod przekopiowany z 
# https://github.com/bowbahdoe/magic-bean/blob/main/src/main/java/dev/mccue/magicbean/MagicBean.java

[Match({'ruleId': 'SENTENCE_WHITESPACE', 'message': 'Add a space between sentences.', 'replacements': [' BeanOps'], 'offsetInContext': 43, 'context': '... will be generated which  Is named [...]BeanOps where [...] is the name of the class. I...', 'offset': 183, 'errorLength': 7, 'category': 'TYPOGRAPHY', 'ruleIssueType': 'whitespace', 'sentence': 'BeanOps where [...] is the name of the class.'}),
 Match({'ruleId': 'COMMA_PARENTHESIS_WHITESPACE', 'message': 'Don’t put a space after the opening parenthesis.', 'replacements': ['{'], 'offsetInContext': 43, 'context': '...tentionPolicy.SOURCE)  public MagicBean {  /  Whether to generate an all args stat...', 'offset': 1071, 'errorLength': 2, 'category': 'TYPOGRAPHY', 'ruleIssueType': 'whitespace', 'sentence': '/\n @Target({ElementType.TYPE})\n @Retention(RetentionPolicy.SOURCE)\n public MagicBean {\n /\n Whether to generate an all args static factory method.'}),
 Match({'ruleId': 'A_NNS', 'message': 'The plural noun “equals” cannot be used 